In [1]:
import requests as req
import numpy as np
import json

In [2]:
class InterestsParser:
    def __init__(self, trees):
        self.trees = trees
        self.count = 0
        
        for tree in trees:
            self.count += _count_interests(tree)
            
    def parse(self, interests_list, prop):
        interests_vec = np.zeros(self.count)
        interests_set = frozenset(interests_list)
        i_p = [0]
        weight = 1 / len(self.trees)

        for tree in self.trees:
            _parse_interests(interests_set, tree, interests_vec, i_p, weight, prop)
        
        return interests_vec

def _count_interests(node):
    count = 1
    if 'children' in node:
        for c in node['children']:
            count = count + _count_interests(c)

    return count

def _parse_interests(i_set, i_node, i_vec, i_p, weight, prop):
    val = 0

    if 'children' in i_node:
        children = i_node['children']
        n_children = len(children)
        for c in children:
            val += _parse_interests(i_set, c, i_vec, i_p, 1 / n_children, prop)

    if prop in i_node:
        if i_node[prop] in i_set:
            val = 1

    i_vec[i_p[0]] = val * weight
    i_p[0] += 1

    return val

In [3]:
class Person:
    def __init__(self, p_id, interests):
        self.p_id = p_id
        self.interests = interests
        
    def __str__(self):
        return 'id: {0} interests: {1}'.format(self.p_id, self.interests)
    
    def __repr__(self):
        return self.__str__()
    
def parse_person(p, interest_parser):
    i = 0
    num = ''
    if len(p) < 1:
        return None

    while p[i] != ' ':
        num = num + p[i]
        i += 1

    p_id = int(num)

    while p[i] != '[':
        i += 1

    s = i + 1

    while p[i] != ']':
        i += 1

    f = i

    interests = interest_parser.parse(p[s:f].split(','), 'name')

    return Person(p_id, interests)

In [4]:
class Topic:
    def __init__(self, t_id, interest, popularity, penalty):
        self.t_id = t_id
        self.interest = interest
        self.popularity = popularity
        self.penalty = penalty
        
    def __str__(self):
        return 'id: {0} interest: {1}'.format(self.t_id, self.interest)
    
    def __repr__(self):
        return self.__str__()
    
def parse_topics(topic_ranks, topic_interests):
    topics = {}
    t_id = 0
    no_match = 0

    for t, r in topic_ranks.items():
        topics[t] = Topic(t_id, None, r, 0)
        t_id += 1

    for t in topic_interests:
        kw = t['keyword']
        if kw in topics:
            topics[kw].interest = interest_parser.parse(t['tags'], 'id')
        else:
            no_match += 1

    topics = list(filter(lambda x: x.interest is not None, topics.values()))
    
    print('Ranked: {}'.format(len(topic_ranks)))
    print('Classified: {}'.format(len(topic_interests)))
    print('Unique: {}'.format(len(topics)))
    print('No match: {}'.format(no_match))
    
    return topics

In [5]:
with open('interests-tree-nested.json') as tree:
    interest_parser = InterestsParser(json.loads(tree.read()))

with open('synthtetic_dataset.lg') as dataset_file:
    raw_data = dataset_file.read()
    
with open('normalizedRanks.json') as topic_ranks_json:
    topic_ranks = json.loads(topic_ranks_json.read())

with open('first.json') as topic_interests_json:
    topic_interests = json.loads(topic_interests_json.read())

lines = raw_data.split('\n')

headers = lines[0:4]
body = lines[5:-1]

In [6]:
persons = [parse_person(p, interest_parser) for p in body]
topics = parse_topics(topic_ranks, topic_interests)

Ranked: 474
Classified: 123
Unique: 89
No match: 12


In [7]:
def reccomend(pers, topics, n):
    ints = np.array([t.interest for t in topics])
    diff = ints - pers.interests
    dist = np.sqrt(np.sum(diff**2,1))
    
    rec = np.argpartition(dist, -n)[-n:]
    return rec, dist[rec]

In [12]:
countem = {}

for pers in persons:
    rec, dist = reccomend(pers, topics, 10)
    
    for i in range(len(rec)):
        print(topic_interests[topics[rec[i]].t_id]['keyword'], dist[i])
        
    print()

#BelieveSurvivors 0.8679982554205624
#PonteExa 0.8864149011929339
#SanAntonio 0.8991146278524947
#NBTSTourGDL 0.8991146278524947
#hcldr 1.1110833329861025
#TimesEvents 1.1020055282588717
#HollywoodShuffle 1.8373223655885207
#TuesdayThoughts 1.0953663995056044
#YoPuedoDarClasesDe 0.9222932977472387
#TheGifted 0.9729521710740332

#BelieveSurvivors 0.8679982554205624
#txlchat 0.9096740782815594
#hcldr 1.1110833329861025
#HollywoodShuffle 1.8968330704925038
#NBTSTourGDL 0.9653309816543686
#PonteExa 0.9404769051686726
#SanAntonio 0.9653309816543686
#TimesEvents 1.1020055282588717
#TuesdayThoughts 1.1503409665352826
#TheGifted 0.9855593768121564

#BelieveSurvivors 0.8679982554205624
#PonteExa 0.8864149011929339
#SanAntonio 0.8991146278524947
#NBTSTourGDL 0.8991146278524947
#hcldr 1.1110833329861025
#TimesEvents 1.1020055282588717
#HollywoodShuffle 1.8373223655885207
#TuesdayThoughts 1.0953663995056044
#YoPuedoDarClasesDe 0.9222932977472387
#TheGifted 0.9729521710740332

#txlchat 0.8040493385

#YoPuedoDarClasesDe 0.9235473685113781
#BelieveSurvivors 0.8693306541402729
#TheGifted 0.9613840980522813
#HollywoodShuffle 1.7764701144923294
#hcldr 1.1121245378348241
#TuesdayThoughts 1.0385978884328764
#TimesEvents 1.1030553019354603

#BelieveSurvivors 0.8112269154553242
#txlchat 0.8112342396431196
#PonteExa 0.8309028306624661
#NBTSTourGDL 0.8444378313199558
#SanAntonio 0.8444378313199558
#HollywoodShuffle 1.8111934220391308
#TuesdayThoughts 1.0509498970511826
#TimesEvents 1.0578678184249364
#hcldr 1.0788260600348034
#TheGifted 0.8816064825474121

#txlchat 0.8360594110924721
#TheGifted 0.9045022594645971
#SanAntonio 0.8683142278411028
#NBTSTourGDL 0.8683142278411029
#PonteExa 0.8551572143821505
#YoPuedoDarClasesDe 0.9060236030850015
#TimesEvents 1.0180971851658458
#HollywoodShuffle 1.8156609268583346
#hcldr 1.0976156044431757
#TuesdayThoughts 1.058630566058878

#BelieveSurvivors 0.8679982554205624
#txlchat 0.9096740782815594
#hcldr 1.1110833329861025
#HollywoodShuffle 1.896833070492

#RegisterToVote 1.0358364975600722
#SANMARCOS 1.0380413236245958
#hcldr 1.0358364975600722
#BelieveSurvivors 1.0800364961722706
#TheGifted 1.166059084630196
#hcldr 1.264191962654825
#YoPuedoDarClasesDe 1.1241364635667734
#TuesdayThoughts 1.2699942562141007
#HollywoodShuffle 1.946486921801103
#TimesEvents 1.2757249099880625

#txlchat 0.9519509611325094
#BelieveSurvivors 0.9648264648192487
#TheGifted 1.033706683467118
#NBTSTourGDL 0.9929130122124492
#SanAntonio 0.9929130122124492
#PonteExa 0.9814277929931208
#TuesdayThoughts 1.173582841118743
#HollywoodShuffle 1.8849993662848448
#TimesEvents 1.1797818951465495
#hcldr 1.1882656725841976

#AfroWorld 0.833908751767104
#txlchat 0.8931745467572711
#PonteExa 0.9110758988188661
#TheGifted 0.918049941670524
#NBTSTourGDL 0.9367104079675572
#hcldr 1.0976156044431757
#HollywoodShuffle 1.8758589561964112
#TimesEvents 1.0180971851658458
#TuesdayThoughts 1.1154171710699086
#SanAntonio 0.9367104079675572

#BelieveSurvivors 0.8679982554205624
#PonteExa 

#TuesdayThoughts 1.0851041452118755
#TheGifted 0.9613840980522812

#SANMARCOS 0.8013085452505114
#hcldr 0.8137654470677635
#RegisterToVote 0.8137654470677635
#YoPuedoDarClasesDe 0.9235473685113781
#BelieveSurvivors 0.8693306541402729
#TheGifted 0.9613840980522813
#HollywoodShuffle 1.7764701144923294
#hcldr 1.1121245378348241
#TuesdayThoughts 1.0385978884328764
#TimesEvents 1.1030553019354603

#RegisterToVote 0.738311228181744
#hcldr 1.0581636236764895
#SANMARCOS 0.7414013822040127
#TimesEvents 1.0486278014366048
#TuesdayThoughts 1.04164851595849
#HollywoodShuffle 1.8058121598672578
#YoPuedoDarClasesDe 0.8578047614126012
#hcldr 0.738311228181744
#BelieveSurvivors 0.7991401961144196
#TheGifted 0.9120526349012583

#YoPuedoDarClasesDe 0.840822782612861
#PonteExa 0.8607292453768504
#BelieveSurvivors 0.8417508112281588
#SanAntonio 0.8738023637004272
#NBTSTourGDL 0.8738023637004272
#HollywoodShuffle 1.8250690211282206
#hcldr 1.0907014392718246
#TimesEvents 1.0814525607271168
#TuesdayThoughts 

#SanAntonio 0.8290145588044207
#PonteExa 0.830229341671883
#YoPuedoDarClasesDe 0.9235473685113782
#BelieveSurvivors 0.8693306541402729
#TheGifted 0.9613840980522813
#HollywoodShuffle 1.7764701144923294
#TimesEvents 1.1030553019354603
#TuesdayThoughts 1.0385978884328764
#hcldr 1.1121245378348241

#YoPuedoDarClasesDe 0.8026090196870023
#txlchat 0.8225684139732176
#PonteExa 0.8419722787004111
#SanAntonio 0.8553321314328218
#NBTSTourGDL 0.8553321314328218
#hcldr 1.0873745775524097
#HollywoodShuffle 1.8094883415237
#TimesEvents 1.0070478316508813
#TuesdayThoughts 1.0480086508155666
#TheGifted 0.8920469685878006

#txlchat 0.8360594110924721
#PonteExa 0.8551572143821505
#SanAntonio 0.8683142278411028
#NBTSTourGDL 0.8683142278411029
#TheGifted 0.9045022594645971
#hcldr 1.0976156044431757
#TuesdayThoughts 1.0391738780702333
#HollywoodShuffle 1.804385844211114
#YoPuedoDarClasesDe 0.9060236030850015
#TimesEvents 1.0180971851658458

#AfroWorld 0.9745188561711646
#PonteExa 1.041317669190334
#Believ

...

#TimesEvents 1.0683917186449037
#HollywoodShuffle 1.8173602161508031
#TuesdayThoughts 1.0615423822541274
#hcldr 1.0891474698221972

#BelieveSurvivors 0.8679982554205624
#txlchat 0.9096740782815594
#hcldr 1.1110833329861025
#HollywoodShuffle 1.8968330704925038
#NBTSTourGDL 0.9653309816543686
#PonteExa 0.9404769051686726
#SanAntonio 0.9653309816543686
#TimesEvents 1.1020055282588717
#TuesdayThoughts 1.1503409665352826
#TheGifted 0.9855593768121564

#BelieveSurvivors 0.8679982554205624
#PonteExa 0.8864149011929339
#SanAntonio 0.8991146278524947
#NBTSTourGDL 0.8991146278524947
#hcldr 1.1110833329861025
#TimesEvents 1.1020055282588717
#HollywoodShuffle 1.8373223655885207
#TuesdayThoughts 1.0953663995056044
#YoPuedoDarClasesDe 0.9222932977472387
#TheGifted 0.9729521710740332

#txlchat 0.8404552060572668
#PonteExa 0.8737017991551821
#BelieveSurvivors 0.8550113614468895
#SanAntonio 0.8865836513315896
#NBTSTourGDL 0.8865836513315896
#HollywoodShuffle 1.8312227968988155
#hcldr 1.100967587910575


#BelieveSurvivors 0.8563639664407174
#TheGifted 0.9625872421773587

#AfroWorld 0.8018128249621415
#txlchat 0.8632848724349667
#PonteExa 0.8817932259938295
#TheGifted 0.8889970165311313
#NBTSTourGDL 0.9082545834702666
#hcldr 1.0734337497568995
#HollywoodShuffle 1.8618127788642682
#TimesEvents 0.9919787691491276
#TuesdayThoughts 1.0916297291286992
#SanAntonio 0.9082545834702666

#YoPuedoDarClasesDe 0.8026090196870023
#TheGifted 0.8205478746391632
#txlchat 0.8225684139732176
#NBTSTourGDL 0.8553321314328218
#PonteExa 0.8419722787004111
#SanAntonio 0.8553321314328218
#hcldr 1.0873745775524097
#HollywoodShuffle 1.8094883415237
#TimesEvents 0.9000353896262527
#TuesdayThoughts 1.0480086508155666

#AfroWorld 0.7992627640751714
#txlchat 0.8609169127961015
#PonteExa 0.8794751009391445
#TheGifted 0.8866977247994753
#NBTSTourGDL 0.9060041656405676
#hcldr 1.0715302958295074
#HollywoodShuffle 1.860715986738869
#TimesEvents 0.989918702826617
#TuesdayThoughts 1.08975805813993
#SanAntonio 0.906004165640

#BelieveSurvivors 0.8679982554205624
#txlchat 0.9096740782815594
#hcldr 1.1110833329861025
#HollywoodShuffle 1.8968330704925038
#NBTSTourGDL 0.9653309816543686
#PonteExa 0.9404769051686726
#SanAntonio 0.9653309816543686
#TimesEvents 1.1020055282588717
#TuesdayThoughts 1.1503409665352826
#TheGifted 0.9855593768121564

#BelieveSurvivors 0.8679982554205624
#PonteExa 0.8864149011929339
#SanAntonio 0.8991146278524947
#NBTSTourGDL 0.8991146278524947
#hcldr 1.1110833329861025
#TimesEvents 1.1020055282588717
#HollywoodShuffle 1.8373223655885207
#TuesdayThoughts 1.0953663995056044
#YoPuedoDarClasesDe 0.9222932977472387
#TheGifted 0.9729521710740332

#hcldr 0.7170169424859628
#YoPuedoDarClasesDe 0.805781160923521
#SanAntonio 0.7482141054393595
#NBTSTourGDL 0.7482141054393595
#BelieveSurvivors 0.7795093836500471
#TheGifted 0.8949021370982478
#HollywoodShuffle 1.7995926684658128
#TimesEvents 1.009577820699855
#TuesdayThoughts 1.0308287182990095
#hcldr 1.089718088646604

#AfroWorld 0.80975645693731

#HollywoodShuffle 1.777905539813833
#hcldr 1.1144160033266965
#TuesdayThoughts 1.0410512065568898
#TimesEvents 1.105365568463328

#YoPuedoDarClasesDe 0.8026090196870023
#txlchat 0.8225684139732176
#PonteExa 0.8419722787004111
#SanAntonio 0.8553321314328218
#NBTSTourGDL 0.8553321314328218
#hcldr 1.0873745775524097
#HollywoodShuffle 1.8094883415237
#TimesEvents 1.0070478316508813
#TuesdayThoughts 1.0480086508155666
#TheGifted 0.8920469685878006

#AfroWorld 0.8044500260764228
#TheGifted 0.8341380590064661
#SanAntonio 0.8969231118388263
#txlchat 0.8657348376700826
#PonteExa 0.8701172182898699
#NBTSTourGDL 0.8969231118388263
#HollywoodShuffle 1.8563112626114688
#TimesEvents 0.9816142616112068
#TuesdayThoughts 1.0822200079805833
#hcldr 1.0754050647536237

#BelieveSurvivors 1.1125801326915978
#txlchat 1.1453909851855473
#SanAntonio 1.1900745709360825
#NBTSTourGDL 1.1900745709360825
#PonteExa 1.1700044399071987
#YoPuedoDarClasesDe 1.1554386644544963
#TheGifted 1.2065408677161664
#TuesdayThough

#TheGifted 0.9729521710740332



In [13]:
topics[0].interest

array([0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.04347826,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.11111111, 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.     